# Import Data/Pkg, Process Data

In [1]:
using Pkg, CategoricalArrays, CSV, DataFrames, Statistics
using StatsBase

In [2]:
data = CSV.read("train.csv", DataFrame);

In [3]:
df = data;

In [4]:
df.Vehicle_Damage = map(x -> x == "Yes" ? 1 : 0, df.Vehicle_Damage);
df.Vehicle_Age = map(x -> x == "> 2 Years" ? 2 : x == "1-2 Year" ? 1 : 0, df.Vehicle_Age);
df[!, "Gender"] = categorical(df[!, "Gender"])
df[!, "Annual_Premium"] = df[!, "Annual_Premium"].*0.012;

In [5]:
t_options = 100:100:1000

100:100:1000

## Split Data

In [6]:
seed = 12345; 
X = df[:, Not([:Response, :Annual_Premium, :id, :Region_Code, :Policy_Sales_Channel])]
y = df.Response
t = df.Annual_Premium
(train_X, train_t, train_y), (test_X, test_t, test_y) = IAI.split_data(
    :policy_maximize, X, t, y, train_proportion=0.5, seed=seed);

In [7]:
train_t_discrete = [min(round(x, digits=-2), 1000) < 100 ? 100 : min(round(x, digits=-2), 1000) for x in train_t]
test_t_discrete = [min(round(x, digits=-2), 1000) < 100 ? 100 : min(round(x, digits=-2), 1000) for x in test_t];

In [8]:
countmap(test_t_discrete)

Dict{Real, Int64} with 10 entries:
  800.0  => 2615
  200.0  => 4109
  500.0  => 32548
  300.0  => 40374
  1000.0 => 1250
  900.0  => 1008
  600.0  => 14369
  700.0  => 5623
  400.0  => 56233
  100    => 32426

## Prescriptive Tree

In [60]:
countmap(train_y)

Dict{Int64, Int64} with 2 entries:
  0 => 167171
  1 => 23383

In [48]:
train_X_df = hcat(train_X, train_t_discrete);

In [103]:
xgb = IAI.XGBoostClassifier(
        random_seed=1, max_depth = 5, num_estimators=250, max_categoric_levels_before_warning=20, )
IAI.fit!(xgb,train_X_df,Array(train_y));

In [104]:
IAI.ROCCurve(xgb, train_X_df, train_y)

[ Warning: `positive_label` keyword argument is required for `ROCCurve`. Defaulting to use 1 for `positive_label`.


ROCCurve with AUC 0.8618:

    Row │ threshold   tpr          fpr       
        │ Float64     Float64      Float64   
────────┼────────────────────────────────────
      1 │ 1.0         0.0          0.0
      2 │ 0.841253    4.27661e-5   0.0
      3 │ 0.825222    8.55322e-5   0.0
      4 │ 0.818416    0.000128298  0.0
      5 │ 0.798742    0.000171064  0.0
      6 │ 0.79538     0.000213831  0.0
      7 │ 0.774942    0.000256597  0.0
      8 │ 0.741671    0.000299363  0.0
      9 │ 0.73707     0.000342129  0.0
     10 │ 0.735062    0.000342129  5.9819e-6
     11 │ 0.734564    0.000384895  5.9819e-6
   ⋮    │     ⋮            ⋮           ⋮
 100684 │ 7.03378e-6  1.0          0.999946
 100685 │ 7.00447e-6  1.0          0.999952
 100686 │ 6.96776e-6  1.0          0.999958
 100687 │ 6.6328e-6   1.0          0.999964
 100688 │ 6.48023e-6  1.0          0.99997
 100689 │ 6.20252e-6  1.0          0.999976
 100690 │ 6.15799e-6  1.0          0.999982
 100691 │ 5.85207e-6  1.0          0.999988
 100692 │ 3.44363e-6  1.0          0.999994
 100693 │ 3.43307e-6  1.0          1.0
 100694 │ 0.0         1.0          1.0
                          100672 rows omitted

In [105]:
xgb_pred=IAI.predict(xgb, train_X_df)
countmap(xgb_pred)

Dict{Int64, Int64} with 2 entries:
  0 => 190153
  1 => 401

In [106]:
IAI.score(xgb, train_X_df, train_y, criterion=:auc)

0.8618371547551407

In [96]:
xgb_prob=IAI.predict_proba(xgb, train_X_df)[!,2];

In [113]:
prescriptive_grid = IAI.GridSearch(
    IAI.OptimalTreePrescriptionMaximizer(
      random_seed=1,
      localsearch=false,
    ),
    max_depth=1:6,
)
# multiple the t(price)revenue with binary var y(1,0) buy or not buy
train_y_revenue = train_y .* train_t_discrete;

In [114]:
IAI.fit!(prescriptive_grid, train_X, train_t_discrete, train_y_revenue)

All Grid Results:

 Row │ max_depth  cp           train_score  valid_score  rank_valid_score 
     │ Int64      Float64      Float64      Float64      Int64            
─────┼────────────────────────────────────────────────────────────────────
   1 │         1  0.030621       0.061242     0.0329424                 6
   2 │         2  0.000367639    0.0721909    0.043583                  5
   3 │         3  9.05484e-5     0.0886814    0.0584221                 4
   4 │         4  1.65282e-5     0.0978411    0.0654498                 3
   5 │         5  2.53188e-5     0.111347     0.0752322                 2
   6 │         6  0.000131518    0.129599     0.0862037                 1

Best Params:
  cp => 0.0001315184036317918
  max_depth => 6

Best Model - Fitted OptimalTreePrescriptionMaximizer:
  1) Split: Vehicle_Damage is 1 or is missing
    2) Split: Age < 27.5
      3) Split: Gender is Male or is missing
        4) Split: Vintage < 207.5
          5) Split: Vintage < 58.5
            6) Split: Age < 25.5
              7) Prescribe: 800.0, 1442 points, error 0.000004344
              8) Prescribe: 900.0, 250 points, error 0.000003822
            9) Split: Vintage < 102.5
              10) Prescribe: 900.0, 1485 points, error 0.000002535
              11) Prescribe: 900.0, 3526 points, error 0.000004974
          12) Split: Age < 24.5
            13) Split: Age < 21.5
              14) Prescribe: 1000.0, 838 points, error 0.000003312
              15) Prescribe: 800.0, 1493 points, error 0.000004796
            16) Split: Age < 26.5
              17) Prescribe: 1000.0, 545 points, error 0.000005516
              18) Prescribe: 1000.0, 215 points, error 0.000002882
        19) Split: Vehicle_Age is 0 or is missing
          20) Split: Vintage < 38.5
            21) Split: Vintage < 14.5
              22) Prescribe: 700.0, 189 points, error 0.000002383
              23) Prescribe: 1000.0, 840 points, error 0.000001431
            24) Split: Vintage < 183.5
              25) Prescribe: 1000.0, 5189 points, error 0.000004348
              26) Prescribe: 1000.0, 4216 points, error 0.000004024
          27) Split: Vintage < 281.5
            28) Split: Age < 22.5
              29) Prescribe: 900.0, 271 points, error 0.000003079
              30) Prescribe: 1000.0, 349 points, error 0.000002794
            31) Prescribe: 500.0, 37 points, error 0.000002769
      32) Split: Age < 52.5
        33) Split: Vintage < 34.5
          34) Split: Gender is Male or is missing
            35) Split: Age < 41.5
              36) Prescribe: 1000.0, 1197 points, error 0.000006334
              37) Prescribe: 800.0, 1493 points, error 0.000006578
            38) Split: Vintage < 18.5
              39) Prescribe: 900.0, 585 points, error 0.000004566
              40) Prescribe: 900.0, 1126 points, error 0.000006099
          41) Split: Previously_Insured < 0.5
            42) Split: Age < 47.5
              43) Prescribe: 1000.0, 35221 points, error 0.00000695
              44) Prescribe: 800.0, 9573 points, error 0.000007644
            45) Prescribe: 300.0, 1653 points, error 0.000003169
        46) Split: Age < 57.5
          47) Split: Vintage < 273.5
            48) Split: Vintage < 254.5
              49) Prescribe: 900.0, 6520 points, error 0.000007407
              50) Prescribe: 800.0, 495 points, error 0.000006345
            51) Split: Age < 55.5
              52) Prescribe: 900.0, 431 points, error 0.000005019
              53) Prescribe: 1000.0, 225 points, error 0.000004209
          54) Split: Previously_Insured < 0.5
            55) Split: Vintage < 129.5
              56) Prescribe: 900.0, 6573 points, error 0.000006654
              57) Prescribe: 1000.0, 9401 points, error 0.000006583
            58) Prescribe: 700.0, 968 points, error 0.000003102
    59) Split: Previously_Insured < 0.5
      60) Split: Vintage < 266.5
        61) Split: Age < 49.5
          62) Split: Vintage < 42.5
            63) Prescribe: 1000.0, 1062 points,

In [99]:
pred_treatments, pred_outcomes = IAI.predict(prescriptive_grid, test_X)

(Real[1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0  …  1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 1000.0, 800.0, 1000.0, 1000.0, 900.0], [353.92188341230946, 353.92188341230946, 0.4917724791218916, 0.4917724791218916, 153.55254851636437, 290.6791643860439, 0.4917724791218916, 0.4917724791218916, 353.92188341230946, 235.6999018153208  …  353.92188341230946, 0.4917724791218916, 353.92188341230946, 265.00565848416755, 353.92188341230946, 265.00565848416755, 8.308620448224247, 353.92188341230946, 265.00565848416755, 44.68966798590759])

In [100]:
countmap(pred_treatments)

Dict{Real, Int64} with 4 entries:
  900.0  => 20640
  700.0  => 464
  1000.0 => 163135
  800.0  => 6316

In [115]:
pred_prob = pred_outcomes./pred_treatments;
pred_binary = pred_prob .>= 0.5;

In [116]:
sum(pred_outcomes.*pred_binary)

0.0

### Prescriptive Tree Evaulation

## Real Data

In [22]:
# Get revenue observed for test set in reality
test_revenue = test_y .* test_t;
print("The real life data suggest the annual revenue would be ", sum(test_revenue))
print("\n")

test_revenue_cut = test_y .* test_t_discrete;
print("If we do the cutoff on real life data, the annual revenue would be ", sum(test_revenue_cut))

The real life data suggest the annual revenue would be 8.851845936e6
If we do the cutoff on real life data, the annual revenue would be 9.0881e6

## Our Prescription

In [33]:
reward_lnr = IAI.NumericClassificationRewardEstimator(
    outcome_estimator=IAI.XGBoostClassifier(num_round=10),
    outcome_insample_num_folds=2,
    reward_estimator=:direct_method,
    estimation_kernel_bandwidth=1,
    random_seed=seed,
)

function get_rewards(reward_lnr, X, t, y, t_options)
  predictions, score = IAI.fit_predict!(reward_lnr, X, t, y, t_options,
                                        outcome_score_criterion=:auc)
  rewards = predictions[:reward]
  for t in t_options
    rewards[!, Symbol(t)] = round.(rewards[!, Symbol(t)] .* t, digits=3)
  end
  rewards, score
end
train_rewards, train_reward_score = get_rewards(reward_lnr, train_X, train_t_discrete,
                                                train_y, t_options)
train_rewards

190554×10 DataFrame
    Row │ 100      200      300      400      500      600      700      800   ⋯
        │ Float64  Float64  Float64  Float64  Float64  Float64  Float64  Float ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │   3.101    8.842   14.141   10.759   14.063   20.654   15.839   25.9 ⋯
      2 │  14.094   22.194   27.6     54.552   70.734   69.247   77.908   49.1
      3 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3
      4 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3
      5 │  28.416   47.233   86.22   126.352  169.403  195.783  267.792  207.8 ⋯
      6 │   2.274    4.586    6.769    9.159   11.161   13.658   15.839   19.8
      7 │  25.744   21.061   58.848   62.675   97.485  192.127  141.875   92.3
      8 │  12.288   13.36    41.945   60.443   58.114   76.321  111.072  138.2
      9 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3 ⋯
     10 │  27.917   37.25   100.471  128.733  159.227  195.783  264.231  504.6
     11 │  27.272   37.25    82.532  117.592  153.286  177.366  260.722  415.0
   ⋮    │    ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋱
 190545 │   2.274    4.586    6.769    9.159   11.161   13.658   15.839   19.8
 190546 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3 ⋯
 190547 │   2.274    4.586    6.769    9.159   11.161   13.658   15.839   19.8
 190548 │  24.331   79.604   94.247  113.403  166.295  236.329  171.686  228.3
 190549 │  25.021   65.113   76.767  110.857  145.554  142.553  163.419  188.3
 190550 │  28.416   47.233   76.287  113.861  163.264  175.329  223.48   207.8 ⋯
 190551 │  28.416   52.421   76.287  107.418  138.169  169.321  283.846  330.5
 190552 │   2.274    4.586    6.769    9.159   11.161   13.658   15.839   19.8
 190553 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3
 190554 │   2.278    4.522    6.737    9.259   11.383   13.723   16.175   19.3 ⋯
                                               3 columns and 190533 rows omitted

In [35]:
train_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.881468
  "400"  => 0.852542
  "1000" => 0.771416
  "600"  => 0.813256
  "800"  => 0.814287
  "700"  => 0.804718
  "100"  => 0.78973
  "200"  => 0.898189
  "500"  => 0.831272
  "900"  => 0.728133

In [ ]:
test_rewards, test_reward_score = get_rewards(reward_lnr, test_X, test_t_discrete,
                                              test_y, t_options)
test_rewards

In [46]:
test_reward_score[:outcome]

Dict{String, Float64} with 10 entries:
  "300"  => 0.880268
  "400"  => 0.851357
  "1000" => 0.799334
  "600"  => 0.81237
  "800"  => 0.787536
  "700"  => 0.800373
  "100"  => 0.78816
  "200"  => 0.89275
  "500"  => 0.827358
  "900"  => 0.768116

In [18]:
function evaluate(recommendations, outcomes, actual_revenue)
  n = length(recommendations)
  pred_revenue = [outcomes[i, recommendations[i]] for i in 1:n]

  improvement = mean(pred_revenue .- actual_revenue) / mean(actual_revenue)
end

evaluate (generic function with 1 method)

In [55]:
function evaluate2(recommendations, outcomes, actual_revenue)
  n = length(recommendations)
  pred_revenue = [outcomes[i, recommendations[i]] for i in 1:n]

  tot_rev = sum(pred_revenue)
end

evaluate2 (generic function with 1 method)

In [37]:
test_revenue = test_y .* test_t_discrete;

In [53]:
recommendations_pres = Symbol.(Int.(IAI.predict(prescriptive_grid, test_X)[1]))

190555-element Vector{Symbol}:
 Symbol("1000")
 Symbol("800")
 Symbol("800")
 Symbol("800")
 Symbol("800")
 Symbol("900")
 Symbol("800")
 Symbol("800")
 Symbol("1000")
 Symbol("900")
 Symbol("900")
 Symbol("800")
 Symbol("900")
 ⋮
 Symbol("800")
 Symbol("1000")
 Symbol("1000")
 Symbol("800")
 Symbol("1000")
 Symbol("1000")
 Symbol("1000")
 Symbol("1000")
 Symbol("1000")
 Symbol("1000")
 Symbol("900")
 Symbol("1000")

In [54]:
evaluate(recommendations_pres, test_rewards, test_revenue)

1.9656464036487267

In [56]:
evaluate2(recommendations_pres, test_rewards, test_revenue)

2.6952091080999993e7